In [2]:
import numpy as np
from scipy.spatial.distance import pdist, squareform
import pandas as pd
import plotly.offline as py
import pickle
import scipy.cluster.hierarchy as sch
from matplotlib import pyplot as plt
import matplotlib.cm as cm
import re
import seaborn as sns
import math
%matplotlib inline
sns.set()

# raysurveyor scripts
from raysurveyor_tutorial.surveyor_scripts.raysurveyor_gentree import read_matrix, build_tree, plotly_heatmap
from raysurveyor_tutorial.surveyor_scripts.matrix_transform import drop_indices, normalize_gram_matrix 
from raysurveyor_tutorial.surveyor_scripts.treeclust_compare import cophentic_correlation_test

# plotly notebook mode
py.init_notebook_mode()

In [3]:
# Read Gram matrix as a pandas dataframe
sim_matrix_global = read_matrix('/project/6007483/projects/SentinelleNord/OutputRaysurveyor_all_b30/RayOutput/Surveyor/SimilarityMatrix.global.tsv')

display(sim_matrix_global)

170004     170013     170022     170032     170034  \
170004                 169000169   67583620   69292012   59469077   41975618   
170013                  67583620  278245031   80810002   76751715   55602796   
170022                  69292012   80810002  339558561  123215417   68673183   
170032                  59469077   76751715  123215417  342191467   62137514   
170034                  41975618   55602796   68673183   62137514  280166925   
...                          ...        ...        ...        ...        ...   
SchirmerM_2016_G89134   33013389   36784142   58225727   54058875   22518049   
SchirmerM_2016_G89182   36209740   39461983   66880881   64452711   28902397   
SchirmerM_2016_G89187   30564842   34306910   58648153   55605943   23491785   
SchirmerM_2016_G89250   28956243   32421176   59928134   56259446   22518675   
SchirmerM_2016_G89275   26599644   29513218   45276136   44049600   15033782   

                          170039     170042     170046     170056    170060  \
170004                  71083125   72943487   69997112   71382605  31496228   
170013                  73499156   73595662   77858465   81437545  49115387   
170022                 114501447  119283217  106387743  119685168  33497410   
170032                  98854541  110599752  107482023  101508508  38282902   
170034                  56871417   62398180   63979573   55315720  31992748   
...                          ...        ...        ...        ...       ...   
SchirmerM_2016_G89134   58397281   55529693   49492555   51671422  11057144   
SchirmerM_2016_G89182   60258476   66528505   60598005   55495011  21098291   
SchirmerM_2016_G89187   47803612   44927925   42581557   45976850  20739898   
SchirmerM_2016_G89250   54609643   52001950   45341297   47128774  12374147   
SchirmerM_2016_G89275   45976444   47226415   41222291   37975370   9598511   

                       ...  SchirmerM_2016_G89074  SchirmerM_2016_G89100  \
170004                 ...               35680915               28179140   
170013                 ...               44358815               33051309   
170022                 ...               47470649               52740232   
170032                 ...               46436997               51320226   
170034                 ...               30947876               21879400   
...                    ...                    ...                    ...   
SchirmerM_2016_G89134  ...               22240669               35680700   
SchirmerM_2016_G89182  ...               27364779               37952428   
SchirmerM_2016_G89187  ...               25722757               31961007   
SchirmerM_2016_G89250  ...               26504772               35387122   
SchirmerM_2016_G89275  ...               20918086               30777028   

                       SchirmerM_2016_G89109  SchirmerM_2016_G89120  \
170004                              31817227               27483994   
170013                              41015365               32865730   
170022                              70971200               57738800   
170032                              70339214               52896870   
170034                              34243195               20799150   
...                                      ...                    ...   
SchirmerM_2016_G89134               34467933               35208560   
SchirmerM_2016_G89182               42418563               39591302   
SchirmerM_2016_G89187               37663929               30190450   
SchirmerM_2016_G89250               46963686               37747459   
SchirmerM_2016_G89275               30745813               26853244   

                       SchirmerM_2016_G89121  SchirmerM_2016_G89134  \
170004                              36683939               33013389   
170013                              35462668               36784142   
170022                              59707797               58225727   
170032                              52137971               5405887

In [5]:
# Neighbor-Joining tree from the gram matrix -> distance matrix

# Get the normalized matrix
norm_mat = normalize_gram_matrix(sim_matrix_global.to_numpy())

# Generate a distance matrix from normalized matrix with a distance function (euclidean)
dist_mat = squareform(pdist(norm_mat, 'euclidean'))
df_dist = pd.DataFrame(dist_mat, index=sim_matrix_global.index, columns=sim_matrix_global.columns)



In [6]:
#rename the samples by there Diet group in the distance matrix
list_new_id = []

for column in df_dist :
    if column[0] == '1' :
        list_new_id.append('Nunavik')
    elif (column[0] == 'O' and (column.split("_")[2] == 'SM32' or column.split("_")[2] == 'SM31' or column.split("_")[2] == 'SM20' or column.split("_")[2] == 'SM02' or column.split("_")[2] == 'HCO67')) or (column[0] == 'P') or (column[0] == 'B'):
        list_new_id.append('Non-Inudustrialized')
    elif (column[0] == 'S' and column[-2] == 'J') or (column[0] == 'O' or column[0] == 'H') or (column[0] == 'S') or (column[0] == 'N') :
        list_new_id.append('Industrialized')

i=0
for column in df_dist :
    df_dist.rename(columns={column : list_new_id[i]}, inplace=True)
    i+=1


df_dist_tr = df_dist.T
j=0
for column in df_dist_tr :
    df_dist_tr.rename(columns={column : list_new_id[j]}, inplace=True)
    j+=1
df_dist = df_dist_tr.T


In [7]:
#labels of samples 
vect_sampleID = pd.Series(df_dist.columns)


In [8]:
#creation of a network labels
network_labels = df_dist.columns

In [10]:
#creation of a color palette to identify the groups
colors = ["#FF7F00", "#00009C", "#871F78"]
network_pal_2 =sns.color_palette(colors)
network_lut_2 = dict(zip(map(str, network_labels.unique()), network_pal_2))

network_colors = pd.Series(network_labels, index=df_dist.columns).map(network_lut_2)


In [11]:
g = sns.clustermap(df_dist,
            # Turn on the clustering
            row_cluster=True, col_cluster=True,
            # Add colored class labels using data frame created from node and network colors
            row_colors = network_colors,
            col_colors = network_colors,
            # Make the plot look better when many rows/cols
            yticklabels=False, xticklabels = False, center = 0,
            figsize=(98, 98), robust=True, method='complete', linewidths=0, 
            # Dendograme leafs
            tree_kws=dict(linewidths=2.5, colors=[(0.1,0.3,0.3,0.5)]*48+[(0.7,0.7,0.3,1)]*49+[(0,0,0,1)]*1+[(0,0.6,1,1)]*169+[(1,0,1,1)]*100+[(0,0,0,1)]*2+[(0,1,1,1)]*25+[(1,1,0,1)]*58+[(0,0,0,1)]*6)
            )


sns.set(font_scale=10)
    
#add a legend for sample groups
for label in vect_sampleID.unique():
    g.ax_col_dendrogram.bar(0, 0, color=network_lut_2[label],
                            label=label, linewidth=0)
g.ax_col_dendrogram.legend(title='Lifestyle', title_fontsize= 70, loc="upper left", 
                           ncol=4, fontsize = 70, bbox_to_anchor=(0.9, 0.9))

/home/fadwameh/jupyter_py3/lib/python3.7/site-packages/seaborn/matrix.py:649: UserWarning:

Clustering large matrix with scipy. Installing `fastcluster` may give better performance.

/home/fadwameh/jupyter_py3/lib/python3.7/site-packages/seaborn/matrix.py:620: ClusterWarning:

scipy.cluster: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix

